In [8]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import plotly.graph_objects as go
import chart_studio.plotly as ply
from scipy.signal import spectrogram, firwin, lfilter, hilbert
from scipy.stats import truncnorm
from utilities.signal_analysis_methods import autocorrelation, autocorrelation_slow

In [82]:
path = 'data/mag_test.csv'
data = pd.read_csv(path)

times = data['Times (s)'].to_numpy()
ch1_voltages = data['Secondary Ch 1 Voltage (V)'].to_numpy()
ch2_voltages = data['Secondary Ch 2 Voltage (V)'].to_numpy()
primary_voltages = data['Primary Voltage (V)'].to_numpy()

sample_rate = int(2e3) # in [Hz]
driving_frequency = 100 # in [Hz]

ch1_AC_voltages = ch1_voltages-np.mean(ch1_voltages)
ch2_AC_voltages = ch2_voltages-np.mean(ch2_voltages)
primary_AC_voltages = primary_voltages-np.mean(primary_voltages)

In [122]:
def gen_envelope(duration, times, mu=5, sigma=1):
    
    lower = 0
    upper = duration
    a, b = (lower - mu) / sigma, (upper - mu) / sigma  # Convert bounds to standard normal units

    return truncnorm(a, b, loc=mu, scale=sigma).pdf(times)

Constructs a synthetic received signal, one component at a time, to test envelope isolation method.
1. Pure co-sinusoidal wave at driving frequency
2. Slow-varying modulatory envelope
3. Out-of-phase component with its own envelope
4. Harmonics
5. Periodic noise (and harmonics)
6. White noise (modeled as i.i.d)

In [190]:
# generating pure co-sinusoidal driving signal and received signal
duration = 10 # in [s]
times = np.linspace(0,duration,duration*sample_rate)
driving_synthetic_voltages = np.cos(2*np.pi*driving_frequency*times)
driving_synthetic_voltages_1st_harmonic = np.cos(4*np.pi*driving_frequency*times)
white_noise = np.random.normal(.1, .05, duration*sample_rate) # mean of 1, sigma of .1
# pure co-sinusoidal received signal
#received_synthetic_voltages = driving_synthetic_voltages
# amplitude modulated co-sinusoidal received signal
#received_synthetic_voltages = gen_envelope(duration, times)*driving_synthetic_voltages
# amplitude modulated co-sinusoidal received signal with small modulated out-of-phase component
#received_synthetic_voltages = gen_envelope(duration, times)*driving_synthetic_voltages + 2*gen_envelope(duration, times, mu=2, sigma=1)*hilbert(driving_synthetic_voltages).imag
# amplitude modulated co-sinusoidal received signal with small modulated out-of-phase component + harmonics
#received_synthetic_voltages = gen_envelope(duration, times)*driving_synthetic_voltages + 2*gen_envelope(duration, times, mu=2, sigma=1)*hilbert(driving_synthetic_voltages).imag \
#                            + gen_envelope(duration, times)*driving_synthetic_voltages_1st_harmonic + 2*gen_envelope(duration, times, mu=2, sigma=1)*hilbert(driving_synthetic_voltages_1st_harmonic).imag
# amplitude modulated co-sinusoidal received signal with small modulated out-of-phase component + white noise
received_synthetic_voltages =  gen_envelope(duration, times)*driving_synthetic_voltages + 2*gen_envelope(duration, times, mu=2, sigma=1)*hilbert(driving_synthetic_voltages).imag + white_noise

# constructing analytic driving signal and computing "locked-in" received signal
driving_analytic_synthetic_voltages = hilbert(driving_synthetic_voltages)
received_locked_synthetic_voltages = driving_analytic_synthetic_voltages*received_synthetic_voltages

# boxcar filtering to isolate envelope
filter_coeffs = firwin(numtaps=int(sample_rate/(.5*driving_frequency)), cutoff=1, fs=sample_rate, window='boxcar')
received_filtered_locked_synthetic_voltages = lfilter(filter_coeffs, 1.0, received_locked_synthetic_voltages)
received_inphase_envelope = 2*received_filtered_locked_synthetic_voltages.real
received_outofphase_envelope = 2*received_filtered_locked_synthetic_voltages.imag

# naive method to isolate envelope via taking magnitude of analytic received signal (for comparison)
received_analytic_magnitude = np.sqrt(hilbert(received_synthetic_voltages).real**2 + hilbert(received_synthetic_voltages).imag**2)

It appears that any harmonics or white noise break both methods for isolating the envelope-- why? Analytically the filtering method at least seems robust... Maybe it's at the point of reconstructing the full envelope from the in-phase and out-of-phase components? Maybe looking at spectra will provide some insight.

In [191]:
fig = go.Figure()
fig.add_trace(go.Scatter(
    x= times,
    y= received_synthetic_voltages, 
    mode='lines', 
    name='Synthetic Received Signal',
    line=dict(color='rebeccapurple', width=2)
))
fig.add_trace(go.Scatter(
    x= times,
    y= received_outofphase_envelope, 
    mode='lines', 
    name='Out-of-Phase Envelope via Filtering',
    line=dict(color='limegreen', width=2)
))
fig.add_trace(go.Scatter(
    x= times,
    y= received_inphase_envelope, 
    mode='lines', 
    name='In-Phase Envelope via Filtering',
    line=dict(color='gold', width=2)
))
fig.add_trace(go.Scatter(
    x= times,
    y = np.sqrt(received_outofphase_envelope**2 + received_inphase_envelope**2),
    mode='lines', 
    name='Full Envelope via Filtering',
    line=dict(color='royalblue', width=2)
))
fig.add_trace(go.Scatter(
    x= times,
    y= received_analytic_magnitude, 
    mode='lines', 
    name='Full Envelope via Magnitude',
    line=dict(color='tomato', width=2, dash='dash')
))
fig.update_layout(
    title='Secondary Coil Voltages',
    xaxis_title='Time (s)',
    yaxis_title='Voltage (V)',
    template='plotly_dark',
    hovermode='x unified',
    #xaxis=dict(range=[0, .4]),
    #yaxis=dict(range=[.8, 1])
)
fig.show()

Spectra before and after filtering

In [192]:
received_locked_synthetic_voltages_fft = np.fft.fftshift(np.fft.fft(received_locked_synthetic_voltages))
received_locked_synthetic_voltages_fftfreq = np.fft.fftshift(np.fft.fftfreq(len(received_locked_synthetic_voltages),1./sample_rate))

received_filtered_locked_synthetic_voltages_fft = np.fft.fftshift(np.fft.fft(received_filtered_locked_synthetic_voltages))
received_filtered_locked_synthetic_voltages_fftfreq = np.fft.fftshift(np.fft.fftfreq(len(received_filtered_locked_synthetic_voltages),1./sample_rate))

fig = go.Figure()
fig.add_trace(go.Scatter(
    x= received_locked_synthetic_voltages_fftfreq,
    y= np.log(np.abs(received_locked_synthetic_voltages_fft)), 
    mode='lines', 
    name='Pre-Filtering',
    line=dict(color='rebeccapurple', width=2)
))
fig.add_trace(go.Scatter(
    x= received_filtered_locked_synthetic_voltages_fftfreq,
    y= np.log(np.abs(received_filtered_locked_synthetic_voltages_fft)), 
    mode='lines', 
    name='Post-Filtering',
    line=dict(color='royalblue', width=2)
))
fig.update_layout(
    title='Locked-In Received Synthetic Signal Spectrum',
    xaxis_title='Frequency (Hz)',
    yaxis_title='Power',
    template='plotly_dark',
    hovermode='x unified',
    xaxis=dict(range=[-300, 300]),
)
fig.show()



Constructs the analytic signal from the primary coil voltage series, computes the locked-in secondary coil voltages by multiplying them with the analytic primary signal, and applies a boxcar filter of period 1/(2*driving_frequency), leaving only the in-phase and out-of-phase envelopes as the real and imaginary components.

In [83]:
primary_analytic_AC_voltages = hilbert(primary_AC_voltages)
ch1_locked_AC_voltages = ch1_AC_voltages * primary_analytic_AC_voltages

filter_coeffs = firwin(numtaps=int(sample_rate/(2*driving_frequency)), cutoff=1, fs=sample_rate, window='boxcar')
ch1_filtered_locked_AC_voltages = lfilter(filter_coeffs, 1.0, ch1_locked_AC_voltages)
ch1_inphase_envelope = 2*ch1_filtered_locked_AC_voltages.real
ch1_quadrature_envelope = 2*ch1_filtered_locked_AC_voltages.imag

In [84]:
# fig = go.Figure()
# fig.add_trace(go.Scatter(
#     x= times,
#     y= ch1_AC_voltages, 
#     mode='lines', 
#     name='Channel 1',
#     line=dict(color='rebeccapurple', width=2)
# ))
# fig.add_trace(go.Scatter(
#     x= times,
#     #y= abs(hilbert(ch1_AC_voltages)), 
#     y= ch1_quadrature_envelope, 
#     mode='lines', 
#     name='Quadrature Envelope',
#     line=dict(color='royalblue', width=2)
# ))
# fig.update_layout(
#     title='Secondary Coil Voltages',
#     xaxis_title='Time (s)',
#     yaxis_title='Voltage (V)',
#     template='plotly_dark',
#     hovermode='x unified',
#     xaxis=dict(range=[85, 85.5]),
#     yaxis=dict(range=[0, 3])
# )
# fig.show()

fig = go.Figure()
fig.add_trace(go.Scatter(
    x= times, 
    y= ch1_AC_voltages, 
    mode='lines', 
    name='Channel 1 Voltage',
    line=dict(color='rebeccapurple', width=2)
))
fig.add_trace(go.Scatter(
    x= times,
    #y= abs(hilbert(ch1_AC_voltages)), 
    y= np.sqrt(ch1_inphase_envelope**2 + ch1_quadrature_envelope**2),     
    mode='lines', 
    name='Full Envelope via Filtering',
    line=dict(color='royalblue', width=2)
))
fig.update_layout(
    title='Secondary Coil Voltages',
    xaxis_title='Time (s)',
    yaxis_title='Voltage (V)',
    template='plotly_dark',
    hovermode='x unified',
    xaxis=dict(range=[75, 100])
)
fig.show()

The more complicated technique vs just taking the magnitude of the hilbert transformed received signal is doing a worse job of reproducing the envelope of the received signal. Is this bc of the harmonics and noise?

In [ ]:

# ch1_fft = np.fft.rfft(ch1_AC_voltages)
# ch1_fftfreqs = np.fft.rfftfreq(len(ch1_AC_voltages),1./sample_rate)

# ch1_inphase_fft = np.fft.rfft(ch1_inphase_AC_voltages)
# ch1_inphase_fftfreqs = np.fft.rfftfreq(len(ch1_inphase_AC_voltages),1./sample_rate)

# ch1_quadrature_fft = np.fft.rfft(ch1_quadrature_AC_voltages)
# ch1_quadrature_fftfreqs = np.fft.rfftfreq(len(ch1_quadrature_AC_voltages),1./sample_rate)

# ch1_welch_inphase_fftfreqs, ch1_welch_inphase_fft  = welch(ch1_inphase_AC_voltages, fs=sample_rate, nperseg=2048)
# ch1_welch_quadrature_fftfreqs, ch1_welch_quadrature_fft  = welch(ch1_quadrature_AC_voltages, fs=sample_rate, nperseg=2048)

# fig = go.Figure(data=go.Scatter(
#     x= ch1_fftfreqs,
#     y= np.log(np.abs(ch1_fft)), 
#     mode='lines', 
#     name='Channel 1',
#     line=dict(color='rebeccapurple', width=2)
# ))
# fig.update_layout(
#     title='Secondary Coil Frequency Spectrum (Channel 1)',
#     xaxis_title='Frequency (Hz)',
#     yaxis_title='Power',
#     template='plotly_dark',
#     hovermode='x unified',
# )
# fig.update_xaxes(range=[1, 350])
# fig.update_yaxes(range=[-10, 11])
# fig.show()

# fig = go.Figure(data=go.Scatter(
#     x= ch1_inphase_fftfreqs,
#     y= np.log(np.abs(ch1_inphase_fft)), 
#     mode='lines', 
#     name='Channel 1',
#     line=dict(color='rebeccapurple', width=2)
# ))
# fig.update_layout(
#     title='In Phase Spectrum',
#     xaxis_title='Frequency (Hz)',
#     yaxis_title='Power',
#     template='plotly_dark',
#     hovermode='x unified'
# )
# fig.update_xaxes(range=[1, 350])
# fig.show()

# fig = go.Figure(data=go.Scatter(
#     x= ch1_quadrature_fftfreqs,
#     y= np.log(np.abs(ch1_quadrature_fft)), 
#     mode='lines', 
#     name='Channel 1',
#     line=dict(color='rebeccapurple', width=2)
# ))
# fig.update_layout(
#     title='Out of Phase Spectrum',
#     xaxis_title='Frequency (Hz)',
#     yaxis_title='Power',
#     template='plotly_dark',
#     hovermode='x unified'
# )
# fig.update_xaxes(range=[1, 350])
# fig.show()

# fig = go.Figure(data=go.Scatter(
#     x= ch1_welch_inphase_fftfreqs,
#     y= np.log(np.abs(ch1_welch_inphase_fft)), 
#     mode='lines', 
#     name='Channel 1',
#     line=dict(color='rebeccapurple', width=2)
# ))
# fig.update_layout(
#     title='Welch Averaged Secondary Coil Frequency Spectrum with Lock-In (Channel 1)',
#     xaxis_title='Frequency (Hz)',
#     yaxis_title='Power',
#     template='plotly_dark',
#     hovermode='x unified'
# )
# fig.update_xaxes(range=[1, 350])
# fig.show()

# fig = go.Figure(data=go.Scatter(
#     x= ch1_welch_quadrature_fftfreqs,
#     y= np.log(np.abs(ch1_welch_quadrature_fft)), 
#     mode='lines', 
#     name='Channel 1',
#     line=dict(color='rebeccapurple', width=2)
# ))
# fig.update_layout(
#     title='Welch Averaged Secondary Coil Frequency Spectrum with Lock-In (Channel 1)',
#     xaxis_title='Frequency (Hz)',
#     yaxis_title='Power',
#     template='plotly_dark',
#     hovermode='x unified'
# )
# fig.update_xaxes(range=[1, 350])
# fig.show()

- test method on synthetics
- add one factor at a time